# Prueba Práctica: Generación de Alertas basadas en Comportamiento de Usuario

The objective of this project is to develop a Python program that monitors a customer orders database and generates an automatic alert when a specific customer records three or more orders in a "returned" or "canceled" state in the same month. The program should be robust, easily integrable with existing systems, and demonstrate proper exception handling.

To achieve this I have used a combination of tools: 

1. **FastAPI** web framework to build a local server and it's API endpoints.
1. **MongoDB Atlas** as a cloud database service in combination with **Pymongo** driver to work and interact with the database

In [1]:
from dotenv import dotenv_values
from pymongo import MongoClient
from fastapi import FastAPI
from bson.binary import UuidRepresentation
config = dotenv_values(".env")

In order to connect the client application to the mongoDB Atlas database I will use the Uniform Resource Identifier (URI) which includes the hostname of the mongoDB Atlas cluster, the authentication credentials and the database name

In [2]:
from fastapi import FastAPI
from routes import router
import nest_asyncio
import uvicorn
import json

#Configure the local server using fastAPI()
app = FastAPI()
app.include_router(router)

#Config the client of mongoDB with the URI and DB_NAME which are contained within the ".env" file
app.mongodb_client =  MongoClient(config["ATLAS_URI"], uuidRepresentation="standard")
app.database = app.mongodb_client[config["DB_NAME"]]
print("Connected to the MongoDB database!")

@app.get("/")
async def root():
    return {"message": "Welcome to the root page!"}

#Start the local server
nest_asyncio.apply()
uvicorn.run(app, port=3000)

Connected to the MongoDB database!


INFO:     Started server process [23604]
INFO:     Waiting for application startup.
INFO:     Application startup complete.
INFO:     Uvicorn running on http://127.0.0.1:3000 (Press CTRL+C to quit)


0
INFO:     127.0.0.1:45416 - "GET /SendAlarm HTTP/1.1" 200 OK
INFO:     127.0.0.1:45416 - "GET /favicon.ico HTTP/1.1" 404 Not Found
printing results
0
INFO:     127.0.0.1:45423 - "GET /initData HTTP/1.1" 200 OK
{'clientName': 'varietysmh', 'shipping_year': '2023', 'shippong_month': '08', 'shipping_Id': ['64e5093257982e3cae08ba38', '64ecf1cbbb4c6187d6ba645e', '64ee469b73db38d2e5f75686'], 'clientEmail': 'varietysmh_81@gmail.com'}
{'clientName': 'tuestioshoes', 'shipping_year': '2023', 'shippong_month': '09', 'shipping_Id': ['64f364329d6233ff381289a8', '64f8d7b0a22cdffd187a09c1', '6500be71669ad8f27627de2a', '6505df24351532bd69ed3531', '6505df96351532bd69ed3535', '650b4bdec65b1c777c316593', '650f118fff00cff833755b87', '650f1190697f9af83aac57b8', '6514501e90b62c005e809aed'], 'clientEmail': 'tuestioshoes_24@gmail.com'}
{'clientName': 'lineal', 'shipping_year': '2023', 'shippong_month': '06', 'shipping_Id': ['6480f0c5b8e3dd5fc8bc36bf', '6480f0c81f89fb38b4b4a3e7', '6480f0c81c58d338a7f99d5c', 

INFO:     Shutting down
INFO:     Waiting for application shutdown.
INFO:     Application shutdown complete.
INFO:     Finished server process [23604]


The "Routes.py" file contains the API endpoints and the different functions called when each of them gets accessed to

In [9]:
import pandas as pd

df = pd.read_csv('db_envios_challenge.csv')

pattern = r"\w+_\d+"

df_order = df['order_vendor_dbname']
df_order.head()

df = df.sort_values(by = ['order_vendor_dbname'])
df = df.groupby(by = ['order_vendor_dbname'])['order_vendor_dbname'].count()

print(df)
df.to_csv("OrdersSort.csv")


order_vendor_dbname
100caps_697473735                44
1astore_620344781                 2
3333digitalstore_1364937057      32
369elitexxx_659958160             2
37zonaurbana_1007604035           2
                                 ..
zunicolau_1197454445             45
zuretecno_500089275              28
zuretex_765848121                42
zyndisonlineshopping_89409166     1
zzamonaviypro_1181713382          1
Name: order_vendor_dbname, Length: 7630, dtype: int64


In [6]:
total_rows = df_order.count()
count_matching_rows = df_order.str.contains(pattern).sum()
count_unique_matching_rows = df_order.str.contains(pattern).sum()
non_matching_rows = ~df_order.str.contains(pattern)
count_non_matching_rows = non_matching_rows.sum()

print("Total number of rows: " + str(total_rows))
print("Pattern-like rows: " + str(count_matching_rows))
print("Unique Pattern-like rows: " + str(count_unique_matching_rows))
print("Non-pattern-like rows: " + str(count_non_matching_rows))

Total number of rows: 631185
Pattern-like rows: 605614
Unique Pattern-like rows: 1
Non-pattern-like rows: 25571


In [31]:
df_order[non_matching_rows].head()

60845    fulanitoperensejoluisantoniodelbarrioconarepi
61322    fulanitoperensejoluisantoniodelbarrioconarepi
75404    fulanitoperensejoluisantoniodelbarrioconarepi
75449    fulanitoperensejoluisantoniodelbarrioconarepi
75752    fulanitoperensejoluisantoniodelbarrioconarepi
Name: order_vendor_dbname, dtype: object

In [48]:
df.isnull().sum()

index                   0
shipping_id             0
shipping_status        71
shipping_date           0
order_vendor_dbname     0
dtype: int64